## Introduction: Business Problem

Yoga has seen a surge in popularity in **Singapore** in the past few years. In this project, we strive to recommend areas in **Singapore** to open a new yoga studio. 
The aim is to avoid opening the studio in areas with high competition. We will highlight urban clusters 
that have a high density of yoga studios to avoid.

As the neighbourhood location data is not readily available in a clean dataset, we will utilize google maps APIs to retrieve them.

In [104]:
google_api_key = "XXXXXX"

The center of Singapore is presumed to be the most accessible place as it is the most centralized location. From this, we determined that the town of Sin Ming is the center of the state and determined the coordinates

In [105]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
    
address = 'Sin Ming, Singapore'
singapore_center = get_coordinates(google_api_key, address)
print('Coordinate of {}: {}'.format(address, singapore_center))

Coordinate of Sin Ming, Singapore: [1.3553878, 103.836408]


In [106]:
!pip install shapely
import shapely.geometry

!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=48, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=48, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('singapore center longitude={}, latitude={}'.format(singapore_center[1], singapore_center[0]))
x, y = lonlat_to_xy(singapore_center[1], singapore_center[0])
print('singapore_center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('singapore_center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
singapore center longitude=103.836408, latitude=1.3553878
singapore_center UTM X=370548.37895831326, Y=149842.45239709734
singapore_center longitude=103.836408, latitude=1.3553878


<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)


We calculate the neighbourhood centers from Sin Ming, for us to explore the vicinity around it. The external radius would be 10km, with a 1km distance apart from each neighbourhood center.

In [107]:
singapore_center_x, singapore_center_y = lonlat_to_xy(singapore_center[1], singapore_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = singapore_center_x - 10000
x_step = 1000
y_min = singapore_center_y - 10000 - (int(21/k)*k*1000 - 20000)/2
y_step = 1000 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 500 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(singapore_center_x, singapore_center_y, x, y)
        if (distance_from_center <= 10001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

364 candidate neighborhood centers generated.


<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)


We use folium to map out the area of exploration. We can see that it covers the entire middle part of Singapore. Which is deemed as satisfactory as we would not like to explore opening a Yoga studio too far out into the ends of the state.

In [108]:
import folium

In [109]:
map_singapore = folium.Map(location=singapore_center, zoom_start=13)
folium.Marker(singapore_center, popup='Singapore').add_to(map_singapore)
for lat, lon in zip(latitudes, longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_singapore) 
    folium.Circle([lat, lon], radius=500, color='blue', fill=False).add_to(map_singapore)
   #folium.Marker([lat, lon]).add_to(map_singapore)
map_singapore

In [110]:

def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(google_api_key, singapore_center[0], singapore_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(singapore_center[0], singapore_center[1], addr))

Reverse geocoding check
-----------------------
Address of [1.3553878, 103.836408] is: Blk 24 Sin Ming Rd, Singapore 570024


We use the google API service to retrieve the longitude and latitude of the neighbourhood centers

In [111]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(google_api_key, lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', Singapore', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


Convert the data retrieved into a dataframe to inspect.

In [112]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address  Latitude   Longitude              X  \
0                          Telok Blangah  1.269207  103.809487  367548.378958   
1                  11 Keppel Hill 098686  1.269211  103.818474  368548.378958   
2            517 Kampong Bahru Rd 099452  1.269215  103.827461  369548.378958   
3  Keppel Terminal Rd M, Keppel Terminal  1.269219  103.836448  370548.378958   
4         Tanjong Pagar Terminal Rd East  1.269223  103.845435  371548.378958   
5                                    MCE  1.269227  103.854422  372548.378958   
6            31 Marina Coastal Dr 018988  1.269231  103.863409  373548.378958   
7           100F Pasir Panjang Rd 118522  1.277034  103.796003  366048.378958   
8                     31 Malan Rd 109436  1.277038  103.804990  367048.378958   
9                             Opp Blk 59  1.277042  103.813977  368048.378958   

               Y  Distance from center  
0  140316.172955           9987.492178  
1  140316.172955           9733.961167  
2  140316.172955           9578.622030  
3  140316.172955           9526.279442  
4  140316.172955           9578.622030  
5  140316.172955           9733.961167  
6  140316.172955           9987.492178  
7  141182.198359           9759.610648  
8  141182.198359           9340.770846  
9  141182.198359           9013.878189

In [113]:
df_locations.shape

(364, 6)

Using Foursquare API service, we will explore the neigbourhood vicinity for yoga studios and gyms as well, as they would be secondary competitors.

In [149]:
client_id = 'XXXX' # your Foursquare ID
client_secret = 'XXXX' # your Foursquare Secret
version = '20180604'
limit = 100
radius = 500

In [150]:

gym_category = '4bf58dd8d48988d175941735' # 'Root' category for all gym-related venues

yoga_studio_categories = ['4bf58dd8d48988d102941735']

def is_gym(categories, specific_filter=None):
    gym_words = ['gym', 'fitness', 'training', 'sports','yoga','boxing','train','exercise','fit']
    gym = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for g in gym_words:
            if g in category_name:
                gym = True
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            gym = True
    return gym, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Singapore', '')
    address = address.replace(', Singapore', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    #version = '20180724'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [152]:

import pickle

def get_gyms(lats, lons):
    gyms = {}
    yoga_studios = {}
    location_gyms = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, gym_category, client_id, client_secret, radius=550, limit=100)
        area_gyms = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_gym_studio, is_yoga = is_gym(venue_categories, specific_filter=yoga_studio_categories)
            if is_gym_studio:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                gym = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_yoga, x, y)
                if venue_distance<=500:
                    area_gyms.append(gym)
                gyms[venue_id] = gym
                if is_yoga:
                    yoga_studios[venue_id] = gym
        location_gyms.append(area_gyms)
        print(' .', end='')
    print(' done.')
    return gyms, yoga_studios, location_gyms

gyms = {}
yoga_studios = {}
location_gyms = []
loaded = False

if not loaded:
    gyms, yoga_studios, location_gyms = get_gyms(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('gyms_550.pkl', 'wb') as f:
        pickle.dump(gyms, f)
    with open('yoga_studios_550.pkl', 'wb') as f:
        pickle.dump(yoga_studios, f)
    with open('location_gyms_550.pkl', 'wb') as f:
        pickle.dump(location_gyms, f)
        

Obtaining venues around candidate locations:

<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


 .

<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


 .

...

 .

<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


 .

<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


 . . . done.


After retrieving the data from foursquare API, we have the following information about gyms and yoga studios in the 10km radius from the middle of Singapore. We can see that there are not many fitness places which are yoga studios in this region of Singapore.

In [153]:
import numpy as np

print('Total number of gyms:', len(gyms))
print('Total number of yoga studios:', len(yoga_studios))
print('Percentage of yoga studios: {:.2f}%'.format(len(yoga_studios) / len(gyms) * 100))
print('Average number of gyms in neighborhood:', np.array([len(r) for r in location_gyms]).mean())

Total number of gyms: 1119
Total number of yoga studios: 132
Percentage of yoga studios: 11.80%
Average number of gyms in neighborhood: 2.7527472527472527


Let's plot a map to visualize where the gyms and yoga studios are.

In [161]:
map_singapore = folium.Map(location=singapore_center, zoom_start=13)
folium.Marker(singapore_center, popup='Singapore').add_to(map_singapore)
for g in gyms.values():
    lat = g[2]; lon = g[3]
    is_yoga = g[6]
    color = 'red' if is_yoga else 'blue'
    label = folium.Popup(str(g[1]), parse_html=True)
    folium.CircleMarker([lat, lon], radius=3, popup=label, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_singapore)
 
map_singapore

Let's calculate the average no. of gyms in each location within 500m and their distance to the nearest yoga studio in the area.

In [162]:
location_gyms_count = [len(g) for g in location_gyms]

df_locations['Gyms in area'] = location_gyms_count

print('Average number of gyms in every area with radius=500m:', np.array(location_gyms_count).mean())

df_locations.head(10)

Average number of gyms in every area with radius=500m: 2.7527472527472527


Address  Latitude   Longitude              X  \
0                          Telok Blangah  1.269207  103.809487  367548.378958   
1                  11 Keppel Hill 098686  1.269211  103.818474  368548.378958   
2            517 Kampong Bahru Rd 099452  1.269215  103.827461  369548.378958   
3  Keppel Terminal Rd M, Keppel Terminal  1.269219  103.836448  370548.378958   
4         Tanjong Pagar Terminal Rd East  1.269223  103.845435  371548.378958   
5                                    MCE  1.269227  103.854422  372548.378958   
6            31 Marina Coastal Dr 018988  1.269231  103.863409  373548.378958   
7           100F Pasir Panjang Rd 118522  1.277034  103.796003  366048.378958   
8                     31 Malan Rd 109436  1.277038  103.804990  367048.378958   
9                             Opp Blk 59  1.277042  103.813977  368048.378958   

               Y  Distance from center  Restaurants in area  \
0  140316.172955           9987.492178                    9   
1  140316.172955           9733.961167                   13   
2  140316.172955           9578.622030                    1   
3  140316.172955           9526.279442                    2   
4  140316.172955           9578.622030                    2   
5  140316.172955           9733.961167                    0   
6  140316.172955           9987.492178                    2   
7  141182.198359           9759.610648                   15   
8  141182.198359           9340.770846                    3   
9  141182.198359           9013.878189                    1   

   Distance to Italian restaurant  Gyms in area  
0                     2033.740178             2  
1                     2048.325485             3  
2                     1774.772675             2  
3                     1122.704199             0  
4                      745.551872             1  
5                     1332.790564             0  
6                     1030.083049             0  
7                     2059.710137             3  
8                     1476.224915             3  
9                     1113.004124             2

In [164]:
distances_to_yoga_studio = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for g in yoga_studios.values():
        g_x = g[7]
        g_y = g[8]
        d = calc_xy_distance(area_x, area_y, g_x, g_y)
        if d<min_distance:
            min_distance = d
    distances_to_yoga_studio.append(min_distance)

df_locations['Distance to Yoga Studio'] = distances_to_yoga_studio
df_locations.head()

Address  Latitude   Longitude              X  \
0                          Telok Blangah  1.269207  103.809487  367548.378958   
1                  11 Keppel Hill 098686  1.269211  103.818474  368548.378958   
2            517 Kampong Bahru Rd 099452  1.269215  103.827461  369548.378958   
3  Keppel Terminal Rd M, Keppel Terminal  1.269219  103.836448  370548.378958   
4         Tanjong Pagar Terminal Rd East  1.269223  103.845435  371548.378958   

               Y  Distance from center  Restaurants in area  \
0  140316.172955           9987.492178                    9   
1  140316.172955           9733.961167                   13   
2  140316.172955           9578.622030                    1   
3  140316.172955           9526.279442                    2   
4  140316.172955           9578.622030                    2   

   Distance to Italian restaurant  Gyms in area  Distance to Yoga Studio  
0                     2033.740178             2               382.845737  
1                     2048.325485             3               481.530744  
2                     1774.772675             2               948.929864  
3                     1122.704199             0              1134.205127  
4                      745.551872             1               899.645033

In [166]:
print('Average distance to closest Yoga Studio from each area center:', df_locations['Distance to Yoga Studio'].mean()/1000, 'km')

Average distance to closest Yoga Studio from each area center: 1.3878447452891058 km


Using a heatmap we can see that we have the most yoga studios in the southern region of Singapore

In [176]:
from folium import plugins
from folium.plugins import HeatMap

map_singapore = folium.Map(location=singapore_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_singapore) #cartodbpositron cartodbdark_matter
HeatMap(yoga_studios_latlons).add_to(map_singapore)
folium.Marker(singapore_center).add_to(map_singapore)
folium.Circle(singapore_center, radius=2500, fill=False, color='white').add_to(map_singapore)
folium.Circle(singapore_center, radius=5000, fill=False, color='white').add_to(map_singapore)
folium.Circle(singapore_center, radius=8000, fill=False, color='white').add_to(map_singapore)
folium.Circle(singapore_center, radius=10000, fill=False, color='white').add_to(map_singapore)
map_singapore

Seeing the trend that the southern region of Singapore is the most popular place to open gyms/yoga studios, we seek to understand the reason contextually. The southern region of Singapore is where the Central Business District is. It is the place that has the highest density of people working. Hence many fitness clubs are open in that area to cater to the growing fitness needs of the working class. 

Hence, we will shift our region of interest towards the Southern region, away from the original center of Sin Ming. We will then explore the southern area of Singapore as a high potential place to open a Yoga studio. The reason for the sparse supply of gyms/yoga studios in other regions could possibly be the lack of demand in the first place.

Despite the higher concentration of competitors, we would still like to explore the untapped areas where the studio could serve the population adequately, without being too near other gyms/yoga studios.

In [200]:
roi_x_min = singapore_center_x
roi_y_max = singapore_center_y
roi_width = 100000
roi_height = 100000
roi_center_x = roi_x_min + 500
roi_center_y = roi_y_max - 6500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_singapore = folium.Map(location=roi_center, zoom_start=14)
HeatMap(yoga_studios_latlons).add_to(map_singapore)
folium.Marker(roi_center).add_to(map_singapore)
folium.Marker(singapore_center).add_to(map_singapore)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_singapore)
map_singapore

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)


Zooming into this region, we will narrow down the neighbourhoods to a 100m radius, while identifying potential locations to open the yoga studio. These locations are deemed as places that do not have more than a gym and yoga studio witin 300m of its vicinity. 

In [263]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

...

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

1431 candidate neighborhood centers generated.


<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

In [264]:
def count_gyms_nearby(x, y, gyms, radius=250):    
    count = 0
    for g in gyms.values():
        g_x = g[7]; g_y = g[8]
        d = calc_xy_distance(x, y, g_x, g_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_gym(x, y, gyms):
    d_min = 100000
    for g in gyms.values():
        g_x = g[7]; g_y = g[8]
        d = calc_xy_distance(x, y, g_x, g_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_gyms_counts = []
roi_yoga_studios_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_gyms_nearby(x, y, gyms, radius=250)
    roi_gyms_counts.append(count)
    distance = find_nearest_gym(x, y, yoga_studios)
    roi_yoga_studios_distances.append(distance)
print('done.')



Generating data on location candidates... done.


In [265]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Gyms nearby':roi_gyms_counts,
                                 'Distance to Yoga Studios':roi_yoga_studios_distances})

df_roi_locations.head(10)

Latitude   Longitude              X              Y  Gyms nearby  \
0  1.273981  103.840490  370998.378958  140842.452397            1   
1  1.273982  103.841389  371098.378958  140842.452397            4   
2  1.274763  103.836445  370548.378958  140929.054937            2   
3  1.274763  103.837344  370648.378958  140929.054937            2   
4  1.274763  103.838243  370748.378958  140929.054937            2   
5  1.274764  103.839141  370848.378958  140929.054937            1   
6  1.274764  103.840040  370948.378958  140929.054937            1   
7  1.274765  103.840939  371048.378958  140929.054937            3   
8  1.274765  103.841838  371148.378958  140929.054937            5   
9  1.274766  103.842736  371248.378958  140929.054937            8   

   Distance to Yoga Studios  
0                445.795424  
1                404.074107  
2                618.885834  
3                554.915719  
4                502.835197  
5                466.642277  
6                406.248637  
7                345.803816  
8                306.794073  
9                297.766565

In [266]:
good_gym_count = np.array((df_roi_locations['Gyms nearby']<=1))
print('Locations with no more than 1 gyms nearby:', good_gym_count.sum())

good_yoga_distance = np.array(df_roi_locations['Distance to Yoga Studios']>=300)
print('Locations with no yoga studios within 300m:', good_yoga_distance.sum())

good_locations = np.logical_and(good_gym_count, good_yoga_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]



Locations with no more than 1 gyms nearby: 553
Locations with no yoga studios within 300m: 763
Locations with both conditions met: 473


Using this information, we visualize the "Good Locations" in a map. The blue regions are the identified areas of potential

In [267]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_singapore = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_singapore)
HeatMap(gyms_latlons).add_to(map_singapore)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_singapore)
folium.Marker(singapore_center).add_to(map_singapore)
folium.Marker(roi_center).add_to(map_singapore)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_singapore) 
map_singapore

Let's remove the heatmap of the other areas and zoom into the areas of potential

In [268]:
map_singapore = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_singapore)
folium.Marker(singapore_center).add_to(map_singapore)
folium.Marker(roi_center).add_to(map_singapore)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_singapore)
map_singapore

Let us now cluster those locations to create centers of zones containing good locations. Those zones, their centers and addresses will be the final result of our analysis.

In [273]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_singapore = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_singapore)
HeatMap(gyms_latlons).add_to(map_singapore)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_singapore)
folium.Marker(singapore_center).add_to(map_singapore)
folium.Marker(roi_center).add_to(map_singapore)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_singapore) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_singapore)
map_singapore

<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
<ipython-input-106-a79b847d2bf6>:18: DeprecationWarning:

In [275]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(google_api_key, lat, lon).replace(', Singapore', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, roi_center_x, roi_center_y)
    print('{}{} => {:.1f}km from Southern central of Singapore'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

671A Klang Ln 211671                               => 1.8km from Southern central of Singapore


<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


Unnamed Road                                       => 0.5km from Southern central of Singapore
284 Bukit Timah Rd 229889                          => 1.7km from Southern central of Singapore


<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


10 Bayfront Ave 018956                             => 2.3km from Southern central of Singapore
175A Chin Swee Rd 169879                           => 1.3km from Southern central of Singapore


...

<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)



Republic Blvd                                      => 2.4km from Southern central of Singapore
30 Kelantan Rd 200030                              => 2.1km from Southern central of Singapore
113 Cavenagh Rd                                    => 1.2km from Southern central of Singapore


<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


103 Dorset Rd 219495                               => 2.2km from Southern central of Singapore
10 Bayfront Ave 018956                             => 2.2km from Southern central of Singapore
25 Gilstead Rd 309070                              => 2.2km from Southern central of Singapore
1 Esplanade Dr                                     => 1.6km from Southern central of Singapore


<ipython-input-106-a79b847d2bf6>:12: DeprecationWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)


In [282]:
map_singapore = folium.Map(location=roi_center, zoom_start=14)

folium.Circle(roi_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_singapore)

for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_singapore) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_singapore)

map_singapore

## Analysis and Conclusion

We identified 15 clusters in the southern region of singapore that have high potential to open a yoga studio.

The initial exploration of the central region of Singapore allowed us to identify that there are ~1100 gyms (fitness centers) in central Singapore, while 11% of them were yoga studios. This represented a good potential to explore opening a new yoga studio. Upon further examination, it was found that the southern region of singapore had the highest concentration of gyms and yoga studios. Contextually, this was explainable because the southern region is the central business district of the country. Many gyms and yoga studios were open there because there was high demand.

Hence, the strategy was to leverage on the clustering effect of businesses, to search for potential locations within the southern region to open the yoga studio, since that would be a place where high demand is expected.

The steps taken was to identify clusters of locations that fit a particular criteria set. In this case, would be to have only 1 gym and NO yoga studios within 300m of the area's vicinity.

In [ ]:
The eventual decision would still have to be based on several other factors (i.e. feasibility, permit)